# 数据分析

In [1]:
import talib
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
def fisher_transform(series: pd.Series, period: int = 10) -> pd.Series:
    """计算费舍尔转换指标"""
    highest = series.rolling(period, min_periods=1).max()
    lowest = series.rolling(period, min_periods=1).min()
    values = np.zeros(len(series))
    fishers = np.zeros(len(series))

    for i in range(1, len(series)):
        values[i] = (
            0.66
            * (
                (series.iloc[i] - lowest.iloc[i]) / (highest.iloc[i] - lowest.iloc[i])
                - 0.5
            )
            + 0.67 * values[i - 1]
        )
        values[i] = max(min(values[i], 0.999), -0.999)
        fishers[i] = (
            0.5 * np.log((1 + values[i]) / (1 - values[i])) + 0.5 * fishers[i - 1]
        )

    return pd.Series(fishers, index=series.index)


def normalize(
    series: pd.Series, period: int = 200, method: str = "zscore"
) -> pd.Series:
    """将时间序列标准化

    Args:
        series: pd.series, 时间序列
        period: int, 回溯窗口
        method: str, 标准化方法，'zscore' or 'ft'

    Returns:
        pd.series，包含标准化数据的时间序列
    """
    if method == "zscore":
        rolling_mean = series.rolling(period).mean()
        rolling_sd = series.rolling(period).std()
        return (series - rolling_mean) / rolling_sd
    elif method == "ft":
        return fisher_transform(series, period)
    else:
        raise ValueError(f"Invalid method '{method}'")


def find_trend_periods(series: pd.Series) -> list:
    """找到连续的1的开始时间和结束时间"""
    periods = []
    start = None

    for i in range(len(series)):
        if series.iloc[i] == 1 and start is None:
            start = series.index[i]
        elif series.iloc[i] == 0 and start is not None:
            end = series.index[i - 1]
            periods.append((start, end))
            start = None

    if start is not None:
        end = series.index[-1]
        periods.append((start, end))

    return periods

## STH Realized Price

In [15]:
# 读取 btcusd 价格
ohlcv = pd.read_csv("./data/btcusd.csv", index_col="datetime", parse_dates=True)

# 读取 sth realized price
metric = pd.read_csv(
    "./data/sth_realized_price.csv", index_col="datetime", parse_dates=True
)

# 合并和清洗数据
df = (
    pd.concat([ohlcv["close"], metric], axis=1, join="outer")
    .rename(columns={"close": "price"})
    .dropna()
)
df

price  sth_realized_price
datetime                                    
2014-09-17    457.334015          548.908069
2014-09-18    424.440002          545.791160
2014-09-19    394.795990          542.147384
2014-09-20    408.903992          539.970448
2014-09-21    398.821014          538.805193
...                  ...                 ...
2025-03-26  86900.882812        93217.144967
2025-03-27  87177.101562        93239.685609
2025-03-28  84353.148438        93125.100057
2025-03-29  82597.585938        93612.585069
2025-03-30  82334.523438        93612.585069

[3838 rows x 2 columns]

In [34]:
# 参数
period = 10  # 标准化指标的窗口
threshold = 2.0  # 生成信号的阈值

# 计算价格偏离实现价格的距离，并进行标准化
data = df.copy()
data["diff"] = data["price"] - data["sth_realized_price"]
data["normalized_diff"] = normalize(data["diff"], period, method="ft")
data.dropna(inplace=True)

peak_periods = find_trend_periods(data["normalized_diff"] >= threshold)
valley_periods = find_trend_periods(data["normalized_diff"] <= -threshold)

data

price  sth_realized_price          diff  normalized_diff
datetime                                                                   
2014-09-17    457.334015          548.908069    -91.574054         0.000000
2014-09-18    424.440002          545.791160   -121.351157        -0.342828
2014-09-19    394.795990          542.147384   -147.351394        -0.791374
2014-09-20    408.903992          539.970448   -131.066456        -0.953753
2014-09-21    398.821014          538.805193   -139.984179        -1.142673
...                  ...                 ...           ...              ...
2025-03-26  86900.882812        93217.144967  -6316.262154         0.948100
2025-03-27  87177.101562        93239.685609  -6062.584046         1.227384
2025-03-28  84353.148438        93125.100057  -8771.951619         0.779494
2025-03-29  82597.585938        93612.585069 -11014.999131         0.166175
2025-03-30  82334.523438        93612.585069 -11278.061631        -0.436454

[3838 rows x 4 columns]

In [37]:
# 创建图表，观察价格和指标的关系
fig = make_subplots(
    rows=3,
    cols=1,
    shared_xaxes=True,
    vertical_spacing=0.05,
    subplot_titles=(
        "<b>Bitcoin Price(USD)</b>",
        "<b>STH Realized Price Diff</b>",
        "<b>Normalized Indicator</b>",
    ),
)

# 比特币价格
fig.add_trace(
    go.Scatter(x=data.index, y=data["price"], name="Bitcoin price"), row=1, col=1
)

# 添加极值区域背景
for x0, x1 in peak_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#FF6B6B",
        opacity=0.2,
        line_width=0,
        row=1,
        col=1,
    )

for x0, x1 in valley_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#38A169",
        opacity=0.2,
        line_width=0,
        row=1,
        col=1,
    )

# 原始指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["sth_realized_price"], name="STH Realized price"),
    row=1,
    col=1,
)

# 价格偏离实现价格的偏差
fig.add_trace(
    go.Scatter(x=data.index, y=data["diff"], fill="tozeroy", name="Deviation"),
    row=2,
    col=1,
)

# 标准化指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["normalized_diff"], name="Normalized Deviation"),
    row=3,
    col=1,
)
for level in [-2, 2]:
    fig.add_hline(
        y=level, row=3, col=1, line_dash="dash", line_color="grey", line_width=0.8
    )

# 更新图表
fig.update_layout(
    title="STH Realized Price",
    width=1000,
    height=1000,
    template="plotly_white",
    showlegend=False,
)

fig.show()

## STH SOPR

In [3]:
# 读取 btcusd 价格
ohlcv = pd.read_csv("./data/btcusd.csv", index_col="datetime", parse_dates=True)

# 读取 sth sopr
metric = pd.read_csv("./data/sth_sopr.csv", index_col="datetime", parse_dates=True)

# 合并和清洗数据
df = (
    pd.concat([ohlcv["close"], metric], axis=1, join="outer")
    .rename(columns={"close": "price"})
    .dropna()
)
df

price  sth_sopr
datetime                          
2014-09-17    457.334015  0.979258
2014-09-18    424.440002  0.917006
2014-09-19    394.795990  0.932153
2014-09-20    408.903992  0.918946
2014-09-21    398.821014  0.940105
...                  ...       ...
2025-03-25  87471.703125  1.000149
2025-03-26  86900.882812  0.997364
2025-03-27  87177.101562  0.997759
2025-03-28  84353.148438  0.993669
2025-03-29  82597.585938  0.988253

[3835 rows x 2 columns]

In [21]:
# # 参数
# period = 10  # 标准化指标的窗口
# threshold = 4.0  # 生成信号的阈值

# # 计算价格偏离实现价格的距离，并进行标准化
# data = df.copy()
# data["smooth_sopr"] = data["sth_sopr"].rolling(10, min_periods=1).mean()
# data["normalized_sopr"] = normalize(data["smooth_sopr"], period, method="ft")
# data.dropna(inplace=True)

# peak_periods = find_trend_periods(data["normalized_sopr"] >= threshold)
# valley_periods = find_trend_periods(data["normalized_sopr"] <= -threshold)

# 参数
period = 200
upper_factor = 2.0
lower_factor = 1.5

# 将布林带应用到指标
data = df.copy()
bband_upper, _, bband_lower = talib.BBANDS(
    data["sth_sopr"], period, upper_factor, lower_factor
)
data["upper_band"] = bband_upper
data["lower_band"] = bband_lower
data.dropna(inplace=True)

peak_periods = find_trend_periods(data["sth_sopr"] > data["upper_band"])
valley_periods = find_trend_periods(data["sth_sopr"] < data["lower_band"])

data

price  sth_sopr  upper_band  lower_band
datetime                                                  
2015-04-04    253.697006  1.001629    1.051142    0.897621
2015-04-05    260.597992  1.003521    1.051418    0.897626
2015-04-06    255.492004  1.000321    1.051738    0.898115
2015-04-07    253.179993  1.009242    1.052238    0.898414
2015-04-08    245.022003  0.995501    1.052494    0.898893
...                  ...       ...         ...         ...
2025-03-25  87471.703125  1.000149    1.030789    0.983107
2025-03-26  86900.882812  0.997364    1.030571    0.983489
2025-03-27  87177.101562  0.997759    1.030090    0.984169
2025-03-28  84353.148438  0.993669    1.029647    0.984766
2025-03-29  82597.585938  0.988253    1.029324    0.985190

[3636 rows x 4 columns]

In [31]:
# 创建图表，观察价格和指标的关系
fig = make_subplots(
    rows=2,
    cols=1,
    shared_xaxes=True,
    vertical_spacing=0.05,
    subplot_titles=(
        "<b>Bitcoin Price(USD)</b>",
        "<b>STH SOPR</b>",
    ),
)

# 比特币价格
fig.add_trace(
    go.Scatter(x=data.index, y=data["price"], name="Bitcoin price"), row=1, col=1
)

# 添加极值区域背景
for x0, x1 in peak_periods:
    line_width = 0 if x0 < x1 else 1.2
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#FF6B6B",
        opacity=0.4,
        line_width=line_width,
        row=1,
        col=1,
    )

for x0, x1 in valley_periods:
    line_width = 0 if x0 < x1 else 1.2
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#38A169",
        opacity=0.4,
        line_width=line_width,
        row=1,
        col=1,
    )

# 指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["sth_sopr"], name="STH SOPR"),
    row=2,
    col=1,
)

# 布林带通道
fig.add_trace(
    go.Scatter(x=data.index, y=data["upper_band"], name="Upper band"),
    row=2,
    col=1,
)
fig.add_trace(
    go.Scatter(x=data.index, y=data["lower_band"], name="Lower band"),
    row=2,
    col=1,
)

# 更新图表
fig.update_layout(
    title="STH SOPR",
    width=1000,
    height=800,
    template="plotly_white",
    showlegend=False,
)

fig.show()

## NRPL

In [9]:
# 读取 btcusd 价格
ohlcv = pd.read_csv("./data/btcusd.csv", index_col="datetime", parse_dates=True)

# 读取 sth nrpl
metric = pd.read_csv("./data/nrpl.csv", index_col="datetime", parse_dates=True)

# 合并和清洗数据
df = (
    pd.concat([ohlcv["close"], metric], axis=1, join="outer")
    .rename(columns={"close": "price"})
    .dropna()
)
df

price         nrpl
datetime                             
2014-09-17    457.334015 -2296.825620
2014-09-18    424.440002 -1921.845934
2014-09-19    394.795990 -1988.424538
2014-09-20    408.903992 -6969.753243
2014-09-21    398.821014 -6349.884731
...                  ...          ...
2025-04-02  82485.710938  6453.323143
2025-04-03  83102.828125  8001.956644
2025-04-04  83843.804688  7754.101582
2025-04-05  83504.796875  7099.285974
2025-04-06  78214.484375  6561.116115

[3844 rows x 2 columns]

In [22]:
# # 参数
# period = 10  # 标准化指标的窗口
# threshold = 4.0  # 生成信号的阈值

# # 标准化指标
# data = df.copy()
# data["normalized_nrpl"] = normalize(data["nrpl"], period, method="ft")
# data.dropna(inplace=True)

# peak_periods = find_trend_periods(data["normalized_nrpl"] >= threshold)
# valley_periods = find_trend_periods(data["normalized_nrpl"] <= -threshold)

# 参数
period = 200
upper_factor = 2.0
lower_factor = 2.0

# 将布林带应用到指标
data = df.copy()
bband_upper, _, bband_lower = talib.BBANDS(
    data["nrpl"], period, upper_factor, lower_factor
)
data["upper_band"] = bband_upper
data["lower_band"] = bband_lower
data.dropna(inplace=True)

peak_periods = find_trend_periods(data["nrpl"] > data["upper_band"])
valley_periods = find_trend_periods(data["nrpl"] < data["lower_band"])

data

price          nrpl    upper_band    lower_band
datetime                                                          
2015-04-04    253.697006 -11260.155052   1904.296179 -24196.120715
2015-04-05    260.597992 -10281.309949   1804.561353 -24176.230734
2015-04-06    255.492004  -9430.024195   1702.953354 -24149.704517
2015-04-07    253.179993  -8844.575881   1606.742848 -24122.055524
2015-04-08    245.022003  -8189.237125   1593.664310 -24121.171825
...                  ...           ...           ...           ...
2025-04-02  82485.710938   6453.323143  34218.155856  -3797.378670
2025-04-03  83102.828125   8001.956644  34204.239976  -3751.117457
2025-04-04  83843.804688   7754.101582  34188.982743  -3702.897620
2025-04-05  83504.796875   7099.285974  34176.219165  -3664.435963
2025-04-06  78214.484375   6561.116115  34166.912089  -3637.074019

[3645 rows x 4 columns]

In [23]:
# 创建图表，观察价格和指标的关系
fig = make_subplots(
    rows=2,
    cols=1,
    shared_xaxes=True,
    vertical_spacing=0.05,
    subplot_titles=(
        "<b>Bitcoin Price(USD)</b>",
        "<b>NRPL</b>",
    ),
)

# 比特币价格
fig.add_trace(
    go.Scatter(x=data.index, y=data["price"], name="Bitcoin price"), row=1, col=1
)

# 添加极值区域背景
for x0, x1 in peak_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#FF6B6B",
        opacity=0.4,
        line_width=0,
        row=1,
        col=1,
    )

for x0, x1 in valley_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#38A169",
        opacity=0.4,
        line_width=0,
        row=1,
        col=1,
    )

# 指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["nrpl"], name="NRPL"),
    row=2,
    col=1,
)

# 布林带通道
fig.add_trace(
    go.Scatter(x=data.index, y=data["upper_band"], name="Upper band"),
    row=2,
    col=1,
)
fig.add_trace(
    go.Scatter(x=data.index, y=data["lower_band"], name="Lower band"),
    row=2,
    col=1,
)

# 更新图表
fig.update_layout(
    title="NRPL",
    width=1000,
    height=800,
    template="plotly_white",
    showlegend=False,
)

fig.show()

## Realized Profit Loss Ratio

In [29]:
# 读取 btcusd 价格
ohlcv = pd.read_csv("./data/btcusd.csv", index_col="datetime", parse_dates=True)

# 读取指标
metric = pd.read_csv(
    "./data/realized_profit_loss_ratio.csv", index_col="datetime", parse_dates=True
)

# 合并和清洗数据
df = (
    pd.concat([ohlcv["close"], metric], axis=1, join="outer")
    .rename(columns={"close": "price"})
    .dropna()
)
df

price  realized_profit_loss_ratio
datetime                                            
2014-09-17    457.334015                    0.498573
2014-09-18    424.440002                    0.186828
2014-09-19    394.795990                    0.115376
2014-09-20    408.903992                    0.253341
2014-09-21    398.821014                    0.375617
...                  ...                         ...
2025-04-03  83102.828125                    2.988043
2025-04-04  83843.804688                    1.465234
2025-04-05  83504.796875                    1.792174
2025-04-06  78214.484375                    0.845261
2025-04-07  79235.335938                    0.944021

[3846 rows x 2 columns]

In [33]:
# 解读方法：使用固定阈值
upper_threshold = 20
lower_threshold = 0.2

data = df.copy()
peak_periods = find_trend_periods(data["realized_profit_loss_ratio"] >= upper_threshold)
valley_periods = find_trend_periods(
    data["realized_profit_loss_ratio"] <= lower_threshold
)

In [34]:
metric_field = "realized_profit_loss_ratio"
metric_name = "Realized Profit Loss Ratio"

# 创建图表，观察价格和指标的关系
fig = make_subplots(
    rows=2,
    cols=1,
    shared_xaxes=True,
    vertical_spacing=0.05,
    subplot_titles=(
        "<b>Bitcoin Price(USD)</b>",
        f"<b>{metric_name}</b>",
    ),
)

# 比特币价格
fig.add_trace(go.Scatter(x=df.index, y=df["price"], name="Bitcoin price"), row=1, col=1)

# 添加极值区域背景
for x0, x1 in peak_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#FF6B6B",
        opacity=0.4,
        line_width=0,
        row=1,
        col=1,
    )

for x0, x1 in valley_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#38A169",
        opacity=0.4,
        line_width=0,
        row=1,
        col=1,
    )

# 指标
fig.add_trace(
    go.Scatter(x=df.index, y=df[metric_field], name=metric_name),
    row=2,
    col=1,
)

for level in [lower_threshold, upper_threshold]:
    fig.add_hline(
        y=level, row=2, col=1, line_dash="dash", line_color="grey", line_width=0.8
    )

# 更新图表
fig.update_layout(
    title=metric_name,
    width=1000,
    height=800,
    template="plotly_white",
    showlegend=False,
)

fig.show()

## STH MVRV

In [6]:
# 读取 btcusd 价格
ohlcv = pd.read_csv("./data/btcusd.csv", index_col="datetime", parse_dates=True)

# 读取指标
metric = pd.read_csv("./data/sth_mvrv.csv", index_col="datetime", parse_dates=True)

# 合并和清洗数据
df = (
    pd.concat([ohlcv["close"], metric], axis=1, join="outer")
    .rename(columns={"close": "price"})
    .dropna()
)
df

price  sth_mvrv
datetime                          
2014-09-17    457.334015     0.846
2014-09-18    424.440002     0.807
2014-09-19    394.795990     0.749
2014-09-20    408.903992     0.764
2014-09-21    398.821014     0.749
...                  ...       ...
2025-04-03  83102.828125     0.888
2025-04-04  83843.804688     0.894
2025-04-05  83504.796875     0.893
2025-04-06  78214.484375     0.877
2025-04-07  79235.335938     0.877

[3846 rows x 2 columns]

In [12]:
# 参数
period = 200  # 标准化指标的窗口
threshold = 2.0  # 生成信号的阈值

# 计算价格偏离实现价格的距离，并进行标准化
data = df.copy()
data["normalized_mvrv"] = normalize(data["sth_mvrv"], period, method="ft")
data.dropna(inplace=True)

peak_periods = find_trend_periods(data["normalized_mvrv"] >= threshold)
valley_periods = find_trend_periods(data["normalized_mvrv"] <= -threshold)

data

price  sth_mvrv  normalized_mvrv
datetime                                           
2014-09-17    457.334015     0.846         0.000000
2014-09-18    424.440002     0.807        -0.342828
2014-09-19    394.795990     0.749        -0.791374
2014-09-20    408.903992     0.764        -1.084432
2014-09-21    398.821014     0.749        -1.471173
...                  ...       ...              ...
2025-04-03  83102.828125     0.888        -3.199944
2025-04-04  83843.804688     0.894        -3.278244
2025-04-05  83504.796875     0.893        -3.352896
2025-04-06  78214.484375     0.877        -3.595789
2025-04-07  79235.335938     0.877        -3.921013

[3846 rows x 3 columns]

In [13]:
# 创建图表，观察价格和指标的关系
fig = make_subplots(
    rows=3,
    cols=1,
    shared_xaxes=True,
    vertical_spacing=0.05,
    subplot_titles=(
        "<b>Bitcoin Price(USD)</b>",
        "<b>STH MVRV</b>",
        "<b>Normalized MVRV</b>",
    ),
)

# 比特币价格
fig.add_trace(
    go.Scatter(x=data.index, y=data["price"], name="Bitcoin price"), row=1, col=1
)

# 添加极值区域背景
for x0, x1 in peak_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#FF6B6B",
        opacity=0.2,
        line_width=0,
        row=1,
        col=1,
    )

for x0, x1 in valley_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#38A169",
        opacity=0.2,
        line_width=0,
        row=1,
        col=1,
    )

# 原始指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["sth_mvrv"], name="STH MVRV"),
    row=2,
    col=1,
)

# 标准化指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["normalized_mvrv"], name="Normalized MVRV"),
    row=3,
    col=1,
)

for level in [-2, 2]:
    fig.add_hline(
        y=level, row=3, col=1, line_dash="dash", line_color="grey", line_width=0.8
    )

# 更新图表
fig.update_layout(
    title="STH MVRV",
    width=1000,
    height=1000,
    template="plotly_white",
    showlegend=False,
)

fig.show()

## STH NUPL

In [3]:
# 读取 btcusd 价格
ohlcv = pd.read_csv("./data/btcusd.csv", index_col="datetime", parse_dates=True)

# 读取指标
metric = pd.read_csv("./data/sth_nupl.csv", index_col="datetime", parse_dates=True)

# 合并和清洗数据
df = (
    pd.concat([ohlcv["close"], metric], axis=1, join="outer")
    .rename(columns={"close": "price"})
    .dropna()
)
df

price  sth_nupl
datetime                          
2014-09-17    457.334015   -0.2780
2014-09-18    424.440002   -0.3760
2014-09-19    394.795990   -0.3132
2014-09-20    408.903992   -0.3448
2014-09-21    398.821014   -0.3408
...                  ...       ...
2025-04-03  83102.828125   -0.0967
2025-04-04  83843.804688   -0.1226
2025-04-05  83504.796875   -0.1023
2025-04-06  78214.484375   -0.1188
2025-04-07  79235.335938   -0.1761

[3842 rows x 2 columns]

In [7]:
# 参数
smooth_period = 10  # 移动平滑窗口
normalized_period = 200  # 标准化窗口
threshold = 2.0  # 生成信号的阈值

# 计算价格偏离实现价格的距离，并进行标准化
data = df.copy()
data["smooth_nupl"] = data["sth_nupl"].rolling(smooth_period, min_periods=1).mean()
data["normalized_nupl"] = normalize(data["smooth_nupl"], normalized_period, method="ft")
data.dropna(inplace=True)

peak_periods = find_trend_periods(data["normalized_nupl"] >= threshold)
valley_periods = find_trend_periods(data["normalized_nupl"] <= -threshold)

data

price  sth_nupl  smooth_nupl  normalized_nupl
datetime                                                        
2014-09-17    457.334015   -0.2780     -0.27800         0.000000
2014-09-18    424.440002   -0.3760     -0.32700        -0.342828
2014-09-19    394.795990   -0.3132     -0.32240        -0.706344
2014-09-20    408.903992   -0.3448     -0.32800        -1.141965
2014-09-21    398.821014   -0.3408     -0.33056        -1.592971
...                  ...       ...          ...              ...
2025-04-03  83102.828125   -0.0967     -0.08687        -2.304428
2025-04-04  83843.804688   -0.1226     -0.08955        -2.274153
2025-04-05  83504.796875   -0.1023     -0.09255        -2.273162
2025-04-06  78214.484375   -0.1188     -0.09719        -2.307003
2025-04-07  79235.335938   -0.1761     -0.10675        -2.404662

[3842 rows x 4 columns]

In [8]:
# 创建图表，观察价格和指标的关系
fig = make_subplots(
    rows=3,
    cols=1,
    shared_xaxes=True,
    vertical_spacing=0.05,
    subplot_titles=(
        "<b>Bitcoin Price(USD)</b>",
        "<b>STH NUPL</b>",
        "<b>Normalized NUPL</b>",
    ),
)

# 比特币价格
fig.add_trace(
    go.Scatter(x=data.index, y=data["price"], name="Bitcoin price"), row=1, col=1
)

# 添加极值区域背景
for x0, x1 in peak_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#FF6B6B",
        opacity=0.2,
        line_width=0,
        row=1,
        col=1,
    )

for x0, x1 in valley_periods:
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#38A169",
        opacity=0.2,
        line_width=0,
        row=1,
        col=1,
    )

# 原始指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["sth_nupl"], name="STH NUPL"),
    row=2,
    col=1,
)

# 标准化指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["normalized_nupl"], name="Normalized NUPL"),
    row=3,
    col=1,
)
for level in [-2, 2]:
    fig.add_hline(
        y=level, row=3, col=1, line_dash="dash", line_color="grey", line_width=0.8
    )

# 更新图表
fig.update_layout(
    title="STH NUPL",
    width=1000,
    height=1000,
    template="plotly_white",
    showlegend=False,
)

fig.show()

## Miner Sell Presure

In [3]:
# 读取 btcusd 价格
ohlcv = pd.read_csv("./data/btcusd.csv", index_col="datetime", parse_dates=True)

# 读取 sth sopr
metric = pd.read_csv(
    "./data/miner_sell_presure.csv", index_col="datetime", parse_dates=True
)

# 合并和清洗数据
df = (
    pd.concat([ohlcv["close"], metric], axis=1, join="outer")
    .rename(columns={"close": "price"})
    .dropna()
)
df

price  miner_sell_presure
datetime                                    
2014-09-17    457.334015            0.757400
2014-09-18    424.440002            0.775895
2014-09-19    394.795990            0.794564
2014-09-20    408.903992            0.797188
2014-09-21    398.821014            0.808384
...                  ...                 ...
2025-04-02  82485.710938            0.368905
2025-04-03  83102.828125            0.340935
2025-04-04  83843.804688            0.344713
2025-04-05  83504.796875            0.325139
2025-04-06  78214.484375            0.311241

[3845 rows x 2 columns]

In [25]:
# 参数
period = 200
upper_factor = 2.0
lower_factor = 1.2

# 将布林带应用到指标
data = df.copy()
bband_upper, _, bband_lower = talib.BBANDS(
    data["miner_sell_presure"], period, upper_factor, lower_factor
)
data["upper_band"] = bband_upper
data["lower_band"] = bband_lower
data.dropna(inplace=True)

peak_periods = find_trend_periods(data["miner_sell_presure"] > data["upper_band"])
valley_periods = find_trend_periods(data["miner_sell_presure"] < data["lower_band"])

data

price  miner_sell_presure  upper_band  lower_band
datetime                                                            
2015-04-04    253.697006            1.821497    2.495864    1.097300
2015-04-05    260.597992            1.776761    2.492589    1.107420
2015-04-06    255.492004            1.772430    2.489356    1.117332
2015-04-07    253.179993            1.790275    2.486357    1.127097
2015-04-08    245.022003            1.801273    2.483299    1.136964
...                  ...                 ...         ...         ...
2025-04-02  82485.710938            0.368905    1.061483    0.370913
2025-04-03  83102.828125            0.340935    1.062186    0.369423
2025-04-04  83843.804688            0.344713    1.062837    0.368040
2025-04-05  83504.796875            0.325139    1.063658    0.366355
2025-04-06  78214.484375            0.311241    1.064528    0.364734

[3646 rows x 4 columns]

In [26]:
# 创建图表，观察价格和指标的关系
fig = make_subplots(
    rows=2,
    cols=1,
    shared_xaxes=True,
    vertical_spacing=0.05,
    subplot_titles=(
        "<b>Bitcoin Price(USD)</b>",
        "<b>Miner Sell Presure</b>",
    ),
)

# 比特币价格
fig.add_trace(
    go.Scatter(x=data.index, y=data["price"], name="Bitcoin price"), row=1, col=1
)

# 添加极值区域背景
for x0, x1 in peak_periods:
    line_width = 0 if x0 < x1 else 1.2
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#FF6B6B",
        opacity=0.4,
        line_width=line_width,
        row=1,
        col=1,
    )

for x0, x1 in valley_periods:
    line_width = 0 if x0 < x1 else 1.2
    fig.add_vrect(
        x0=x0,
        x1=x1,
        fillcolor="#38A169",
        opacity=0.4,
        line_width=line_width,
        row=1,
        col=1,
    )

# 指标
fig.add_trace(
    go.Scatter(x=data.index, y=data["miner_sell_presure"], name="Miner Sell Presure"),
    row=2,
    col=1,
)

# 布林带通道
fig.add_trace(
    go.Scatter(x=data.index, y=data["upper_band"], name="Upper band"),
    row=2,
    col=1,
)
fig.add_trace(
    go.Scatter(x=data.index, y=data["lower_band"], name="Lower band"),
    row=2,
    col=1,
)

# 更新图表
fig.update_layout(
    title="Bitcoin Miner Sell Presure",
    width=1000,
    height=800,
    template="plotly_white",
    showlegend=False,
)

fig.show()

In [23]:
# # 参数
# smooth_period = 7  # 移动平滑窗口
# normalized_period = 10  # 标准化窗口
# threshold = 2.0  # 生成信号的阈值

# # 计算价格偏离实现价格的距离，并进行标准化
# data = df.copy()
# data["smooth_msp"] = (
#     data["miner_sell_presure"].rolling(smooth_period, min_periods=1).mean()
# )
# data["normalized_msp"] = normalize(data["smooth_msp"], normalized_period, method="ft")
# data.dropna(inplace=True)

# peak_periods = find_trend_periods(data["normalized_msp"] >= threshold)
# valley_periods = find_trend_periods(data["normalized_msp"] <= -threshold)

# data

In [24]:
# # 创建图表，观察价格和指标的关系
# fig = make_subplots(
#     rows=3,
#     cols=1,
#     shared_xaxes=True,
#     vertical_spacing=0.05,
#     subplot_titles=(
#         "<b>Bitcoin Price(USD)</b>",
#         "<b>Miner Sell Presure</b>",
#         "<b>Normalized MSP</b>",
#     ),
# )

# # 比特币价格
# fig.add_trace(
#     go.Scatter(x=data.index, y=data["price"], name="Bitcoin price"), row=1, col=1
# )

# # 添加极值区域背景
# for x0, x1 in peak_periods:
#     fig.add_vrect(
#         x0=x0,
#         x1=x1,
#         fillcolor="#FF6B6B",
#         opacity=0.2,
#         line_width=0,
#         row=1,
#         col=1,
#     )

# for x0, x1 in valley_periods:
#     fig.add_vrect(
#         x0=x0,
#         x1=x1,
#         fillcolor="#38A169",
#         opacity=0.2,
#         line_width=0,
#         row=1,
#         col=1,
#     )

# # 原始指标
# fig.add_trace(
#     go.Scatter(x=data.index, y=data["miner_sell_presure"], name="Miner Sell Presure"),
#     row=2,
#     col=1,
# )

# # 标准化指标
# fig.add_trace(
#     go.Scatter(x=data.index, y=data["normalized_msp"], name="Normalized MSP"),
#     row=3,
#     col=1,
# )
# for level in [-threshold, threshold]:
#     fig.add_hline(
#         y=level, row=3, col=1, line_dash="dash", line_color="grey", line_width=0.8
#     )

# # 更新图表
# fig.update_layout(
#     title="Miner Sell Presure",
#     width=1000,
#     height=1000,
#     template="plotly_white",
#     showlegend=False,
# )

# fig.show()